<a href="https://colab.research.google.com/github/merliou/term_paper_css/blob/main/bert_08.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [32]:
# Installiere die notwendigen Bibliotheken
!pip install bertopic
!pip install umap-learn
!pip install pandas
!pip install numpy

# Importiere die notwendigen Bibliotheken
import pandas as pd
import numpy as np
from bertopic import BERTopic
from umap import UMAP
from hdbscan import HDBSCAN

# Lade die CSV-Datei
data = pd.read_csv("10_data_covs_avg_no_doubles.csv", header=0)

## draw 10 percent random sample
#np.random.seed(161)
#data = data.sample(frac=0.1)

data['ort'] = data['ort']
data['bundesland'] = data['bundesland']
data['rating_rez'] = data['bewertung']
data['rezension'] = data['rezension']
data['traeger'] = data['Traeger']
data['typ'] = data['EinrichtungsTyp']
data['versorgungsstufe'] = data['Allgemeine_Notfallversorgung']
data['bettenzahl'] = data['INSG']
data['rating_avg'] = data['rating']
data['number_of_ratings'] = data['total_ratings']

data['bundesland'].value_counts()
data['rating_rez'].value_counts()
data['traeger'].value_counts()
data['typ'].value_counts()
data['versorgungsstufe'].value_counts()
data['rating_avg'].value_counts()


# Zeige die ersten 3 Zeilen der Daten an
print(data.iloc[0:3])

## Bereite die Daten vor (falls nötig)
## In diesem Fall verwenden wir die Spalte 'rezension' für die Textanalyse
#documents = data['rezension'].tolist()
#
## Erstelle das UMAP-Modell
#umap_model = UMAP(random_state=1337)
#
## Erstelle das BERTopic-Modell
#topic_model = BERTopic(umap_model=umap_model)
#
## Führe das Modell auf den Dokumenten aus
#topics, probs = topic_model.fit_transform(documents)
#
## Zeige die häufigsten Themen an
#topic_info = topic_model.get_topic_info()
#print(topic_info)

Data cleaning

In [33]:
# Überprüfe auf fehlende Werte in der Spalte 'rezension'
print(data['rezension'].isnull().sum())

# Entferne Zeilen mit fehlenden Werten
data = data.dropna(subset=['rezension'])

## Oder ersetze fehlende Werte durch einen leeren String
#data['rezension'] = data['rezension'].fillna("")

# Extrahiere die Dokumente
documents = data['rezension'].tolist()

# Überprüfe die ersten 5 Dokumente
print(documents[:5])

# Überprüfe den Datentyp der Spalte 'rezension'
print(data['rezension'].dtype)

data['rezension'] = data['rezension'].astype(str)

0
['Von A-Z positiv. Teil 1\nVom Reinigungspersonal bis zu den Ärzten gibt es nur positives zu berichten.\nReibungsloser Ablauf von den Rettungskräften bis zur Notaufnahme.\nDer Personalmangel ist vorhanden aber für einen Patienten kaum spürbar.\nNatürlich entstehen längere Wartezeiten und das Personal steht dann auch mal unter Strom…\nEs ist manchmal aber auch kein Verständnis seitens des Patienten vorhanden.\nWenn ein Notfall per Hubschrauber angekündigt wird und in der Zeit Patienten nach dem Weg fragen oder ähnliche Fragen gestellt werden und das Personal in der Notaufnahme sich 100 mal dafür entschuldigen muss, das es im Moment nicht reagieren kann… und trotzdem freundlich bleibt… ich glaube da würde so mancher Mensch anders reagieren.\nDie Station A2 war stets bemüht es für jeden Patienten so angenehm wie möglich zu machen was zu einer schnelleren Genesung beiträgt.\nAuch wenn ungeduldige Patienten manchmal das Optimum fordern - auch wenn es nicht gewollt ist aber die Situation e

Modell ausführen

In [35]:
## Extrahiere die Dokumente
#documents = data['rezension'].tolist()

# Erstelle das BERTopic-Modell
topic_model = BERTopic(min_topic_size=15) # Minimalanzahl an Topics einstellen

# Führe das Modell auf den Dokumenten aus
topics, probs = topic_model.fit_transform(documents)

# Zeige die Themeninformationen an
topic_info = topic_model.get_topic_info()
print(topic_info)

KeyboardInterrupt: 

Modell 2: Dok's in einzelne Sätze gesplittet

In [56]:
import nltk
nltk.download('punkt')
nltk.download('punkt_tab')

def split_into_sentences(text):
  sentences = nltk.sent_tokenize(text, language='german') # use language='german' for German text.
  return sentences

# Wende die Funktion auf alle Rezensionen an
split_documents = [split_into_sentences(doc) for doc in documents]
# flatten the list for Bertopic
all_sentences = [sentence for sublist in split_documents for sentence in sublist]

# Erstelle und trainiere das BERTopic-Modell mit den Sätzen
topic_model = BERTopic(min_topic_size=15)
topics, probs = topic_model.fit_transform(all_sentences)

# Zeige die Themeninformationen an
topic_info = topic_model.get_topic_info()
print(topic_info)

In [22]:
# auf 20 Topics reduzieren NACHDEM es initial cluster gefunden hat
topic_model = BERTopic(nr_topics=20, min_topic_size=9) # Oder nr_topics=15, etc.
topics, probs = topic_model.fit_transform(all_sentences)

In [43]:
# Zeige die Dokumentinformationen an
document_info = topic_model.get_document_info(documents)
print(document_info)

# Visualisiere die Ergebnisse
# Themen-Distanz
topic_model.visualize_topics()

In [44]:
# Wort-Scores
topic_model.visualize_barchart() # erste 10 topics

In [45]:
# Themen-Similarität
topic_model.visualize_heatmap()

In [46]:
# Themen-Hierarchie
topic_model.visualize_hierarchy()

In [ ]:
# Zeige spezifische Themen an (z.B. Thema 49)
specific_topic = topic_model.get_topic(49)
print(specific_topic)

# Zeige repräsentative Dokumente für spezifische Themen an (z.B. Thema 49 und 82)
representative_docs_49 = topic_model.get_representative_docs(topic=49)
representative_docs_82 = topic_model.get_representative_docs(topic=82)
print(representative_docs_49)
print(representative_docs_82)

[('station', np.float64(0.03075882698078743)), ('klinik', np.float64(0.027546367922963364)), ('bis', np.float64(0.0220624117142804)), ('31', np.float64(0.019609307870642197)), ('sehr', np.float64(0.019021210113480475)), ('vom', np.float64(0.017089858739553477)), ('mich', np.float64(0.015538967779543769)), ('an', np.float64(0.015220149515462798)), ('stationr', np.float64(0.014620596392466096)), ('ihr', np.float64(0.013943521142597984))]
['Eine sehr gute Klinik. Ich war 1 Woche stationär auf St. 31 und wurde sehr gut betreut. Ein großes Lob und Dankeschön an Dr. M. Stockbauer und OÄ Dr. Wallisch für die hervorragende Behandlung.\nAlle Mitarbeiter/innen auf St. 31 geben ihr bestes und waren überaus freundlich und bemüht.\nDer einzigste Minuspunkt ist das Essen, leider nicht sehr gut, aber auch das überlebt man :-)\nViele Grüße,  Claudia Grimm', 'Ich war vor einer Woche in der Klinik. Angefangen bei der Patientenaufnahme über das OP-Team bis zur Station sehr freundliche und hilfsbereite Me

Fine tuning

In [108]:
# Benutzerdefinierte Themen-Labels setzen
topic_model.set_topic_labels({49: "Krankenhaus Erfahrungen", 82: "Psychiatrische Behandlung"})
print(topic_model.get_topic_info(49))
print(topic_model.get_topic_info(82))

# Themen pro Klasse (falls eine Klassenspalte vorhanden ist)
classes = data['rating_rez'] # bei versorgungsstufe gibts Probleme

topics_per_class = topic_model.topics_per_class(documents, classes=classes)
topic_model.visualize_topics_per_class(topics_per_class, top_n_topics=31)

##################### kMeans ##################
# Ändere das Clustering-Modell zu KMeans
from sklearn.cluster import KMeans

cluster_model = KMeans(n_clusters=15)  # Verwende KMeans-Clustering mit ... Themen
topic_model_kmeans = BERTopic(hdbscan_model=cluster_model)
# topicsKmeans, probsKmeans = topic_model_kmeans.fit_transform(documents) # auf dokumentenebene
topicsKmeans, probsKmeans = topic_model_kmeans.fit_transform(all_sentences) # satzebene (sentenizer)

# Zeige die Themeninformationen für das KMeans-Modell an
topic_info_kmeans = topic_model_kmeans.get_topic_info()
print(topic_info_kmeans)

# Output in Tabellenform
html_table = topic_info_kmeans.to_html()
with open("model_06_k15_topic_info.html", "w", encoding='utf-8') as f:
    f.write(html_table)

#stopword entfernung NACH modellerstellung
from sklearn.feature_extraction.text import CountVectorizer
vectorizer_model = CountVectorizer(stop_words="german", min_df=2, ngram_range=(1, 2))

# Zeige die Dokumentinformationen für das KMeans-Modell an
document_info_kmeans = topic_model_kmeans.get_document_info(all_sentences)
print(document_info_kmeans)

# Output in Tabellenform
html_table = document_info_kmeans.to_html()
with open("model_05_k20_document_info.html", "w", encoding='utf-8') as f:
    f.write(html_table)

# Wort-Scores
topic_model_kmeans.visualize_barchart() # erste 10 topics

# Themen-Distanz
topic_model_kmeans.visualize_topics()

# Themen-Hierarchie
topic_model_kmeans.visualize_hierarchy()

# Themen-Similarität
topic_model_kmeans.visualize_heatmap()

# Themen pro Klasse (falls eine Klassenspalte vorhanden ist)
# classes = data['rating_rez']
sentence_index = [i for i, doc in enumerate(split_documents) for _ in range(len(doc))]
classes = pd.Series([data['rating_rez'].iloc[i] for i in sentence_index])
# classes = pd.Series([data['traeger'].iloc[i] for i in sentence_index]) #auswählen welche covariate
# classes = pd.Series([data['versorgungsstufe'].iloc[i] for i in sentence_index]) # bei versorgungsstufe gibts Probleme

topics_per_class = topic_model_kmeans.topics_per_class(all_sentences, classes=classes)
topic_model.visualize_topics_per_class(topics_per_class, top_n_topics=15)


################ Seeded ############################
## Geführte Themenmodelle (Guided Topic Models)
seed_topic_list = [["freundlich", "empathisch", "kümmern", "nett"],
                   ["kompetent", "professionell", "fachlich"],
                   ["diagnose", "behandlung", "untersuchung"],
                   ["station", "ablauf", "organisation"],
                   ["op", "narkose"],
                   ["sauber", "hygiene", "putzen", "reinigung"],
                   ["zimmer", "bett", "bad", "ausstattung", "wlan"],
                   ["essen", "mahlzeiten", "küche", "cafeteria", "getränke"],
                   ["schmerzen", "schmerzmittel", "übelkeit", "beschwerden"],
                   ["information", "kommunikation", "gespräch", "aufklärung"],
                   ["zufrieden", "unzufrieden", "empfehlen", "weiterempfehlen", "positiv", "negativ", "katastrophe"],
                   ["danke", "dankeschön", "dank"]]

topic_model_guided = BERTopic(seed_topic_list=seed_topic_list)
topics_guided, probs_guided = topic_model_guided.fit_transform(all_sentences)

# Zeige die Themeninformationen für das geführte Modell an
topic_info_guided = topic_model_guided.get_topic_info()
print(topic_info_guided)

# Visualisiere die Ergebnisse des geführten Modells
topic_model_guided.visualize_barchart(n_words=8, top_n_topics=12)

# Zeige die Dokumentinformationen für das geführte Modell an
document_info_guided = topic_model_guided.get_document_info(documents)
print(document_info_guided)